In [1]:
import numpy as np
import plotly.graph_objects as go
def save_figure_to_file(fig, path, file_name):
    fig.write_image(path + '/' + file_name + '.svg')

In [2]:
n = 4

Z = np.random.standard_normal((n,n))

Q, R = np.linalg.qr(Z,mode='complete')

# test
np.testing.assert_array_less(np.eye(n) - np.dot(Q,Q.T), 1e-14)

d = 0.1 + np.random.random((n,))
d = np.sort(d)
D = np.diag(d)

H = np.dot(Q, np.dot(D,Q.T))
U, S, VT = np.linalg.svd(H, full_matrices=True)

# test symmetry
np.linalg.norm(H - H.T)

# test evals
w, v = np.linalg.eig(H)
w = np.sort(w)
np.testing.assert_array_less(w-d, 1e-14)

beta = 0.1

D = np.diag([beta**k for k in range(n)])

Hb = np.dot(D, np.dot(H, D))

U, S, VT = np.linalg.svd(Hb, full_matrices=True)

for i in range(n):
    if U[i,i] < 0:
        U[:,i] = -U[:,i]
        VT[i,:] = -VT[i,:]

print('Hb=')
print(Hb)
print('U=')
print(U)
print('V=')
print(VT.T)
print('Sigma=')
print(S/S[0])

Hb=
[[ 7.78721673e-01 -1.07051401e-02 -2.49862455e-04  4.46940935e-05]
 [-1.07051401e-02  4.51042298e-03 -1.97050251e-04 -1.57350085e-05]
 [-2.49862455e-04 -1.97050251e-04  4.77849687e-05 -8.60630057e-07]
 [ 4.46940935e-05 -1.57350085e-05 -8.60630057e-07  5.70715454e-07]]
U=
[[ 9.99904404e-01  1.37937014e-02  9.56752670e-04  2.88202633e-05]
 [-1.38231113e-02  9.98825738e-01  4.61273371e-02  5.32314838e-03]
 [-3.17293018e-04 -4.63142436e-02  9.98106289e-01  4.04811735e-02]
 [ 5.76574374e-05 -3.44531319e-03 -4.06840096e-02  9.99166121e-01]]
V=
[[ 9.99904404e-01  1.37937014e-02  9.56752670e-04  2.88202633e-05]
 [-1.38231113e-02  9.98825738e-01  4.61273371e-02  5.32314838e-03]
 [-3.17293018e-04 -4.63142436e-02  9.98106289e-01  4.04811735e-02]
 [ 5.76574374e-05 -3.44531319e-03 -4.06840096e-02  9.99166121e-01]]
Sigma=
[1.00000000e+00 5.61297589e-03 4.93970786e-05 5.82005587e-07]


In [3]:
x0 = np.random.standard_normal((n,1))

D = np.diag([beta**(-k) for k in range(n)])

alpha = 1

w, v = np.linalg.eig( alpha * Hb )
print(w)

w, v = np.linalg.eig( alpha * np.dot(D, Hb) )
print(w)

x = x0.copy()
print('|x0|=',np.linalg.norm((x)))

k_iter = 10000
print('number of iterations=',k_iter)
G = np.eye(n) - alpha * np.dot(D, Hb)
norm_x_0 = np.zeros(1 + int((k_iter-1)/100))
for k in range(k_iter):
    x = np.dot(G, x)
    if k%100 == 0:
        norm_x_0[int(k/100)] = np.linalg.norm((x))

print('x=',np.linalg.norm((x)))
        
x = x0.copy()
k_iter = int(k_iter/beta**(n-1))
print('number of iterations=',k_iter)
G = np.eye(n) - alpha * Hb
norm_x_1 = np.zeros(1 + int((k_iter-1)/100))
for k in range(k_iter):
    x = np.dot(G, x)
    if k%100 == 0:
        norm_x_1[int(k/100)] = np.linalg.norm((x))     

print('x=',np.linalg.norm((x)))

[7.78869747e-01 4.37177711e-03 3.84738901e-05 4.53306545e-07]
[7.80289606e-01 4.46031316e-02 3.83776532e-03 4.44612173e-04]
|x0|= 2.9274439322964425
number of iterations= 10000
x= 0.025985875499751416
number of iterations= 9999999
x= 0.023686230593092706


In [4]:
beta = 0.1
n = 4
# beta = 0.9
# n = 100
m = n-1
print('Estimated condition number: {:.2e}\n'.format(beta**(2*m)))
print('Estimated number of iterations with Adagrad: {:.2e}\n'.format(beta**(-m)))
print('Estimated number of iterations without Adagrad: {:.2e}\n'.format(beta**(-2*m)))

Estimated condition number: 1.00e-06

Estimated number of iterations with Adagrad: 1.00e+03

Estimated number of iterations without Adagrad: 1.00e+06



In [5]:
fig = go.Figure()
fig.add_trace(go.Scatter(y=norm_x_1,name='Gradient Descent'))
fig.add_trace(go.Scatter(y=norm_x_0,name='Adagrad'))
fig.update_layout(height=400, width=600, xaxis_type="log", yaxis_type="log", 
                  xaxis_title='iteration', yaxis_title='error')
fig.show()

In [6]:
save_figure_to_file(fig,'../Slides/Deep_Learning','fig6')